In [12]:
import re
import numpy as np
import pandas as pd
from pprint import pprint
import string
import pickle

# Gensim
import gensim
import gensim.corpora as corpora
from gensim.utils import simple_preprocess
from gensim.models import CoherenceModel

# Stop words
from nltk.corpus import stopwords
stop_words = stopwords.words('english')

import re, nltk, spacy

# Sklearn
from sklearn.decomposition import LatentDirichletAllocation, TruncatedSVD
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import train_test_split
from pprint import pprint

# Plotting tools
import pyLDAvis
import pyLDAvis.gensim  # don't skip this
import pyLDAvis.sklearn
import matplotlib.pyplot as plt
%matplotlib inline

pd.set_option('display.max_colwidth', -1)

import warnings
warnings.filterwarnings("ignore",category=DeprecationWarning)
import bigfloat
bigfloat.exp(5000,bigfloat.precision(100))

BigFloat.exact('2.9676283840236670689662968052896e+2171', precision=100)

In [2]:
#read linkedin general sample, google, twitter, and facebook data scientists
linkedinDatascientist = pd.read_csv('Datasets/datascientist.csv')
facebookDatascientist = pd.read_csv('Datasets/facebookdatasci.csv')
twitterDatascientist = pd.read_csv('Datasets/twitterdatasci.csv')
googleDatascientist = pd.read_csv('Datasets/googledatasci.csv')

In [8]:
combindedDatascientist1 = linkedinDatascientist.append(facebookDatascientist)
combindedDatascientist2 = combindedDatascientist1.append(twitterDatascientist)
combindedDatascientist = combindedDatascientist2.append(googleDatascientist)

Unnamed: 0                            name  \
0    2           Christopher Cotton               
1    3           Aaron Baker                      
2    4           Abdallah MJ Musmar               
3    5           Abhinav Gupta                    
4    6           Allison Chau                     
5    7           Ajay Anand                       
6    8           Ajay Saini                       
7    9           Ajnu Jacob                       
8    10          Alexander Gude                   
9    11          Alexander Wolf                   
10   12          Aliki Mavromoustaki              
11   13          Al Christopher                   
12   14          Ameesha Chhabra                  
13   15          Amit Yadav                       
14   16          Alex Simonoff                    
15   17          Andrew Dove                      
16   18          Andrew Noble                     
17   19          Anirban Majumder                 
18   20          Ankit Dhingra                    
19   21          Ankur Khurana                    
20   22          Anne Mandich, PhD                
21   23          Anshuman Kumar                   
22   24          Aparupa Das Gupta                
23   25          Arghavan Bahadorinejad           
24   26          Arijit Ghosh                     
25   27          Arjun Mishra                     
26   28          Arvind Ramesh                    
27   29          Binghui Ouyang                   
28   30          Brian W.                         
29   31          Brandon Kurkela                  
..   ..                      ...                  
327  329         Xiaoxiao Wang                    
328  330         Eric Li                          
329  331         Xiaoyu Dai                       
330  332         Eric Bai                         
331  333         Xiongying Yuan                   
332  334         Jackie (Rongjing) Xiang          
333  335         Xuesi Feng                       
334  336         Yading Song, PhD                 
335  337         Yang Zhang                       
336  338         Chen-Yu Yang                     
337  339         Yang Gu                          
338  340         Yaohui Zeng                      
339  341         Yash Sharma                      
340  342         Jingxin Ye                       
341  343         Yi Deng                          
342  344         Yipeng Yang                      
343  345         Yiren Lu                         
344  346         Yoann ASSAYAG                    
345  347         Yuan Jin                         
346  348         Yuao Hu                          
347  349         Yue Shi                          
348  350         Yuexi Ma                         
349  351         Yunzhu (Anny) Chen               
350  352         Zachary Cain                     
351  353         Zhanyong Wang                    
352  354         Zhen Qin                         
353  355         Zhenyu Lu                        
354  356         Zhifan (Vivienne) Zhang, Ph.D.   
355  357         Zhuo Z.                          
356  358         Zynab Ali                        

                                                                                                                                                                                                                                                                                                                                                                                                                                                           certifications  \
0    NaN                                                                                                                                                                                                                                                                                                                                                                                     

In [9]:
##clean combined data scientists

# delete first unnamed row
del combindedDatascientist['Unnamed: 0'];

#remove profiles with no summary and convert summary section to string
combindedDatascientist = combindedDatascientist[pd.notnull(combindedDatascientist['summary'])]
combindedDatascientist['summary'] = combindedDatascientist['summary'].astype('str');

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


name  \
0    Christopher Cotton        
1    Aaron Baker               
2    Abdallah MJ Musmar        
3    Abhinav Gupta             
4    Allison Chau              
5    Ajay Anand                
6    Ajay Saini                
7    Ajnu Jacob                
9    Alexander Wolf            
11   Al Christopher            
12   Ameesha Chhabra           
13   Amit Yadav                
14   Alex Simonoff             
16   Andrew Noble              
17   Anirban Majumder          
18   Ankit Dhingra             
19   Ankur Khurana             
21   Anshuman Kumar            
25   Arjun Mishra              
28   Brian W.                  
31   Binh (Brad) Nguyen        
32   Brent Ferrier             
33   Bill Ulammandakh          
34   Callum McDonald           
35   Carolyn (Haozhi) Xu       
37   Chi Cheng                 
38   Charlie Carson            
40   Chengzhi Zong             
41   Chhavi Choudhury          
42   Chintan Trivedi           
..               ...           
309  Vetri Venthan Elango      
311  Kaushik Subramanian       
312  Vladimir Khalatyan        
313  Jan Vlachy                
314  Wan Chen                  
315  Wei-Hong Chuang           
316  Wenfei Zou                
317  William Beason            
319  William Lane              
320  Wynn Vonnegut             
321  Xia Li                    
323  Xiaofan Xu                
325  Xiaojun Di                
326  Xiaoli Yan                
327  Xiaoxiao Wang             
328  Eric Li                   
331  Xiongying Yuan            
332  Jackie (Rongjing) Xiang   
333  Xuesi Feng                
336  Chen-Yu Yang              
337  Yang Gu                   
338  Yaohui Zeng               
341  Yi Deng                   
342  Yipeng Yang               
344  Yoann ASSAYAG             
347  Yue Shi                   
350  Zachary Cain              
352  Zhen Qin                  
353  Zhenyu Lu                 
356  Zynab Ali                 

                                                                                                                                                                                                                                                                                                                                                                                                                                                           certifications  \
0    NaN                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
1    SAS Certified Predictive Modeler Using SAS Enterprise Miner 7; SAS Certified Statistical Business Analyst Using SAS 9: Regression and Modeling; SAS Certified Base Programmer for SAS 9; Lean Six Sigma Yellow Belt                                                                                                                                                                                                                                                    
2    Deep Learning Specialization; Sequence Models; Convolutional Neural Networks; Improving Deep Neural Networks: Hyperparameter tuning, Regularization and Optimization; Structuring Machine Learning Projects; Neural Networks and Deep Learning; Tableau 10 for Data Scientists; Data Mining  Specialization; HP Vertica Solutions HP2-N36; SAS Statistical Business Analyst Using SAS 9: Regression and Modeling                                                       
3    Machine Learning: Classification; Machine Learning: Regression | University of Washington; Customer Analytics | University of Pennsylvania; Introduction to Natural Language Processing | Univ

In [10]:
##Write function to keep only data scientists
combindedDatascientist = combindedDatascientist[combindedDatascientist['headline'].str.contains("Data Scientist")]
combindedDatascientist

name  \
0    Christopher Cotton        
1    Aaron Baker               
2    Abdallah MJ Musmar        
3    Abhinav Gupta             
4    Allison Chau              
5    Ajay Anand                
6    Ajay Saini                
7    Ajnu Jacob                
9    Alexander Wolf            
11   Al Christopher            
12   Ameesha Chhabra           
13   Amit Yadav                
14   Alex Simonoff             
16   Andrew Noble              
17   Anirban Majumder          
18   Ankit Dhingra             
19   Ankur Khurana             
21   Anshuman Kumar            
25   Arjun Mishra              
28   Brian W.                  
31   Binh (Brad) Nguyen        
32   Brent Ferrier             
33   Bill Ulammandakh          
34   Callum McDonald           
35   Carolyn (Haozhi) Xu       
37   Chi Cheng                 
38   Charlie Carson            
40   Chengzhi Zong             
41   Chhavi Choudhury          
42   Chintan Trivedi           
..               ...           
184  Matt Dawson               
186  Matthew Burns             
192  Michael Beaumier          
193  Michael Dezube            
228  Pei-Chun (Heather) Chen   
231  Phil Culliton             
237  David Quinn               
242  Ravinder Singh            
243  Walter Reade              
246  Reza Hosseini             
255  Roy Sasson                
256  Ruoyi Jiang               
263  Samanth Reddy             
274  Shi Zhong                 
279  Shuchao B.                
284  Sneha Chatterjee          
289  Stoyan Georgiev           
291  Sjef van Stiphout         
292  Simon Han                 
300  Tom Ferriss               
302  Tong Wang                 
313  Jan Vlachy                
317  William Beason            
320  Wynn Vonnegut             
321  Xia Li                    
323  Xiaofan Xu                
331  Xiongying Yuan            
338  Yaohui Zeng               
341  Yi Deng                   
353  Zhenyu Lu                 

                                                                                                                                                                                                                                                                                                                                                                                                                                                           certifications  \
0    NaN                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
1    SAS Certified Predictive Modeler Using SAS Enterprise Miner 7; SAS Certified Statistical Business Analyst Using SAS 9: Regression and Modeling; SAS Certified Base Programmer for SAS 9; Lean Six Sigma Yellow Belt                                                                                                                                                                                                                                                    
2    Deep Learning Specialization; Sequence Models; Convolutional Neural Networks; Improving Deep Neural Networks: Hyperparameter tuning, Regularization and Optimization; Structuring Machine Learning Projects; Neural Networks and Deep Learning; Tableau 10 for Data Scientists; Data Mining  Specialization; HP Vertica Solutions HP2-N36; SAS Statistical Business Analyst Using SAS 9: Regression and Modeling                                                       
3    Machine Learning: Classification; Machine Learning: Regression | University of Washington; Customer Analytics | University of Pennsylvania; Introduction to Natural Language Processing | Univ

In [18]:
## function to clean summary text
def cleanSummary(a, value):
    for i in value:
        a = a.replace(i,' ', regex=True)
    return a;
    
value = [r'\n', r'\...', r'✔', r'►', r'\t', r'\-', r'\'', r'\"', r'\/', r'\:',
         r'\•', r'\...', r'\... ', r'\!', r'\,', r'\.', r'\(', r'\)', r'\|', r'\+', 
         r'\@', r'\_', r'\;', r'\>', r'\<', r'I', r'http', r'www', r'\■']

combindedDatascientist['summary'] = cleanSummary(combindedDatascientist['summary'], value)

combindedDatascientist

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  # This is added back by InteractiveShellApp.init_path()


name  \
0    Christopher Cotton        
1    Aaron Baker               
2    Abdallah MJ Musmar        
3    Abhinav Gupta             
4    Allison Chau              
5    Ajay Anand                
6    Ajay Saini                
7    Ajnu Jacob                
9    Alexander Wolf            
11   Al Christopher            
12   Ameesha Chhabra           
13   Amit Yadav                
14   Alex Simonoff             
16   Andrew Noble              
17   Anirban Majumder          
18   Ankit Dhingra             
19   Ankur Khurana             
21   Anshuman Kumar            
25   Arjun Mishra              
28   Brian W.                  
31   Binh (Brad) Nguyen        
32   Brent Ferrier             
33   Bill Ulammandakh          
34   Callum McDonald           
35   Carolyn (Haozhi) Xu       
37   Chi Cheng                 
38   Charlie Carson            
40   Chengzhi Zong             
41   Chhavi Choudhury          
42   Chintan Trivedi           
..               ...           
184  Matt Dawson               
186  Matthew Burns             
192  Michael Beaumier          
193  Michael Dezube            
228  Pei-Chun (Heather) Chen   
231  Phil Culliton             
237  David Quinn               
242  Ravinder Singh            
243  Walter Reade              
246  Reza Hosseini             
255  Roy Sasson                
256  Ruoyi Jiang               
263  Samanth Reddy             
274  Shi Zhong                 
279  Shuchao B.                
284  Sneha Chatterjee          
289  Stoyan Georgiev           
291  Sjef van Stiphout         
292  Simon Han                 
300  Tom Ferriss               
302  Tong Wang                 
313  Jan Vlachy                
317  William Beason            
320  Wynn Vonnegut             
321  Xia Li                    
323  Xiaofan Xu                
331  Xiongying Yuan            
338  Yaohui Zeng               
341  Yi Deng                   
353  Zhenyu Lu                 

                                                                                                                                                                                                                                                                                                                                                                                                                                                           certifications  \
0    NaN                                                                                                                                                                                                                                                                                                                                                                                                                                                                    
1    SAS Certified Predictive Modeler Using SAS Enterprise Miner 7; SAS Certified Statistical Business Analyst Using SAS 9: Regression and Modeling; SAS Certified Base Programmer for SAS 9; Lean Six Sigma Yellow Belt                                                                                                                                                                                                                                                    
2    Deep Learning Specialization; Sequence Models; Convolutional Neural Networks; Improving Deep Neural Networks: Hyperparameter tuning, Regularization and Optimization; Structuring Machine Learning Projects; Neural Networks and Deep Learning; Tableau 10 for Data Scientists; Data Mining  Specialization; HP Vertica Solutions HP2-N36; SAS Statistical Business Analyst Using SAS 9: Regression and Modeling                                                       
3    Machine Learning: Classification; Machine Learning: Regression | University of Washington; Customer Analytics | University of Pennsylvania; Introduction to Natural Language Processing | Univ

In [19]:
#Randomly create a training dataset
combindedDatascientistTrain = combindedDatascientist.sample(frac=0.8, random_state=200);
combindedDatascientistTest = combindedDatascientist.drop(combindedDatascientistTrain.index);

In [20]:
#Prepare summary column to be preprocessed
datascienceSummary = combindedDatascientistTrain[['summary']];
datascienceSummary = datascienceSummary.summary.values.tolist();

datascienceSummary

['  am a community organizer  rogue scholar  and ex software engineer  spend most of my time organizing for Resource Generation and CARW in Seattle  reading  writing  and trying to practice radical care for myself and other people   love reviously    worked for Google as a software engineer on Kubernetes for about a year after graduating from Oberlin College in Oberlin  OH  where   studied math  was also a Data Science for Social Good Fellow at the University of Chicago and a software engineer during the 2012 Obama campaign with the folks who eventually became AMG  ',
 'Yimin Yang is a Computer Science Ph  with over 10 years of academic and 4 years of industrial R&D experience in multiple domains  such as machine learning  deep learning  and computer vision he        has published over 20 research papers in international journals and conferences   ',
 '   Strong 2 years of experience research internship academic projects  in Predictive modeling  Machine learning  Data Mining  Statistic

In [21]:
#Preprocess Linkedin Data using gensim
def sent_to_words(sentences):
    for sentence in sentences:
        yield(gensim.utils.simple_preprocess(str(sentence), deacc=True))  # deacc=True removes punctuations

datascienceSum = list(sent_to_words(datascienceSummary))
print(datascienceSum)

[['am', 'community', 'organizer', 'rogue', 'scholar', 'and', 'ex', 'software', 'engineer', 'spend', 'most', 'of', 'my', 'time', 'organizing', 'for', 'resource', 'generation', 'and', 'carw', 'in', 'seattle', 'reading', 'writing', 'and', 'trying', 'to', 'practice', 'radical', 'care', 'for', 'myself', 'and', 'other', 'people', 'love', 'reviously', 'worked', 'for', 'google', 'as', 'software', 'engineer', 'on', 'kubernetes', 'for', 'about', 'year', 'after', 'graduating', 'from', 'oberlin', 'college', 'in', 'oberlin', 'oh', 'where', 'studied', 'math', 'was', 'also', 'data', 'science', 'for', 'social', 'good', 'fellow', 'at', 'the', 'university', 'of', 'chicago', 'and', 'software', 'engineer', 'during', 'the', 'obama', 'campaign', 'with', 'the', 'folks', 'who', 'eventually', 'became', 'amg'], ['yimin', 'yang', 'is', 'computer', 'science', 'ph', 'with', 'over', 'years', 'of', 'academic', 'and', 'years', 'of', 'industrial', 'experience', 'in', 'multiple', 'domains', 'such', 'as', 'machine', 'le

In [22]:
# Build the bigram and trigram models
bigram = gensim.models.Phrases(datascienceSum, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[datascienceSum], threshold=100)  

# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)

# See trigram example
print(trigram_mod[bigram_mod[datascienceSum[0]]])

/anaconda3/lib/python3.6/site-packages/gensim/models/phrases.py:494: UserWarning: For a faster implementation, use the gensim.models.phrases.Phraser class
  warnings.warn("For a faster implementation, use the gensim.models.phrases.Phraser class")


['am', 'community', 'organizer', 'rogue', 'scholar', 'and', 'ex', 'software', 'engineer', 'spend', 'most', 'of', 'my', 'time', 'organizing', 'for', 'resource', 'generation', 'and', 'carw', 'in', 'seattle', 'reading', 'writing', 'and', 'trying', 'to', 'practice', 'radical', 'care', 'for', 'myself', 'and', 'other', 'people', 'love', 'reviously', 'worked', 'for', 'google', 'as', 'software', 'engineer', 'on', 'kubernetes', 'for', 'about', 'year', 'after', 'graduating', 'from', 'oberlin', 'college', 'in', 'oberlin', 'oh', 'where', 'studied', 'math', 'was', 'also', 'data', 'science', 'for', 'social', 'good', 'fellow', 'at', 'the', 'university', 'of', 'chicago', 'and', 'software', 'engineer', 'during', 'the', 'obama', 'campaign', 'with', 'the', 'folks', 'who', 'eventually', 'became', 'amg']


In [23]:
#change words to its root using lemmatization
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append(" ".join([token.lemma_ if token.lemma_ not in ['-PRON-'] else '' for token in doc if token.pos_ in allowed_postags]))
    return texts_out

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
# Run in terminal: python3 -m spacy download en
nlp = spacy.load('en', disable=['parser', 'ner'])

# Do lemmatization keeping only Noun, Adj, Verb, Adverb
data_lemmatized = lemmatization(datascienceSum, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])


print(data_lemmatized[:2])

['be community organizer rogue scholar software engineer spend most  time organize resource generation carw seattle reading writing try practice radical care other people love reviously work software engineer kubernete year graduate oberlin college oberlin where study math be also data science social good fellow university chicago software engineer obama campaign folk who eventually become amg', 'yimin be computer science year academic year industrial experience multiple domain such machine learn deep learning computer vision have publish research paper international journal conference']


In [24]:
#Create vector of words and remove stop words
vectorizer = CountVectorizer(analyzer='word',       
                             min_df=2,                        # minimum reqd occurences of a word
                             max_df=30,
                             stop_words='english',             # remove stop words
                             lowercase=True,                   # convert all words to lowercase
                             token_pattern='[a-zA-Z0-9]{3,}',  # num chars > 3
                             # max_features=50000,             # max number of uniq words
                            )

data_vectorized = vectorizer.fit_transform(data_lemmatized)

In [25]:
# Materialize the sparse data
data_dense = data_vectorized.todense()

# Compute Sparsicity = Percentage of Non-Zero cells
print("Sparsicity: ", ((data_dense > 0).sum()/data_dense.size)*100, "%")

Sparsicity:  1.3230215477406488 %


In [26]:
# Build LDA Model
lda_model = LatentDirichletAllocation(n_topics=3,               # Number of topics
                                      max_iter=10,               # Max learning iterations
                                      learning_method='online',   
                                      random_state=100,          # Random state
                                      batch_size=60,            # n docs in each learning iter
                                      evaluate_every = -1,       # compute perplexity every n iters, default: Don't
                                      n_jobs = -1,               # Use all available CPUs
                                     )
lda_output = lda_model.fit_transform(data_vectorized)

print(lda_model)  # Model attributes

LatentDirichletAllocation(batch_size=60, doc_topic_prior=None,
             evaluate_every=-1, learning_decay=0.7,
             learning_method='online', learning_offset=10.0,
             max_doc_update_iter=100, max_iter=10, mean_change_tol=0.001,
             n_components=10, n_jobs=-1, n_topics=3, perp_tol=0.1,
             random_state=100, topic_word_prior=None,
             total_samples=1000000.0, verbose=0)


In [ ]:
#pickle the model for later use
filename = 'lda_model.sav'
pickle.dump(lda_model, open(filename, 'wb'))

#load the model
loaded_model = pickle.load(open(filename, 'rb'))

In [27]:
# Log Likelyhood: Higher the better
print("Log Likelihood: ", lda_model.score(data_vectorized))

# Perplexity: Lower the better. Perplexity = exp(-1. * log-likelihood per word)
print("Perplexity: ", lda_model.perplexity(data_vectorized))

# See model parameters
pprint(lda_model.get_params())

Log Likelihood:  -74992.71054338056
Perplexity:  1489.7782388690496
{'batch_size': 60,
 'doc_topic_prior': None,
 'evaluate_every': -1,
 'learning_decay': 0.7,
 'learning_method': 'online',
 'learning_offset': 10.0,
 'max_doc_update_iter': 100,
 'max_iter': 10,
 'mean_change_tol': 0.001,
 'n_components': 10,
 'n_jobs': -1,
 'n_topics': 3,
 'perp_tol': 0.1,
 'random_state': 100,
 'topic_word_prior': None,
 'total_samples': 1000000.0,
 'verbose': 0}


In [29]:
#Create Document - Topic Matrix
lda_output = lda_model.transform(data_vectorized)

# column names
topicnames = ["Topic" + str(i) for i in range(lda_model.n_topics)]

# index names
docnames = ["Doc" + str(i) for i in range(len(datascienceSum))]

# Make the pandas dataframe
df_document_topic = pd.DataFrame(np.round(lda_output, 2), columns=topicnames, index=docnames)

# Get dominant topic for each document
dominant_topic = np.argmax(df_document_topic.values, axis=1)
df_document_topic['dominant_topic'] = dominant_topic

# Styling
def color_green(val):
    color = 'green' if val > .1 else 'black'
    return 'color: {col}'.format(col=color)

def make_bold(val):
    weight = 700 if val > .1 else 400
    return 'font-weight: {weight}'.format(weight=weight)

# Apply Style
df_document_topics = df_document_topic.head(10).style.applymap(color_green).applymap(make_bold)
df_document_topics

In [30]:
df_topic_distribution = df_document_topic['dominant_topic'].value_counts().reset_index(name="Num Documents")
df_topic_distribution.columns = ['Topic Num', 'Num Documents']
df_topic_distribution

Topic Num  Num Documents
0  2          243          
1  0          130          
2  1          72

In [31]:
pyLDAvis.enable_notebook()
panel = pyLDAvis.sklearn.prepare(lda_model, data_vectorized, vectorizer, mds='tsne')
panel

PreparedData(topic_coordinates=            Freq  cluster  topics           x           y
topic                                                    
2      53.702756  1        1      -372.142456 -195.243271
0      31.394533  1        2      -437.769562 -443.703552
1      14.902712  1        3      -620.127258 -262.638367, topic_info=     Category       Freq            Term      Total  loglift  logprob
term                                                                 
218   Default  31.000000  classification  31.000000  30.0000  30.0000
1294  Default  27.000000  scikit          27.000000  29.0000  29.0000
161   Default  22.000000  boost           22.000000  28.0000  28.0000
518   Default  23.000000  experienced     23.000000  27.0000  27.0000
1342  Default  21.000000  simulation      21.000000  26.0000  26.0000
791   Default  14.000000  leader          14.000000  25.0000  25.0000
294   Default  12.000000  content         12.000000  24.0000  24.0000
1397  Default  19.000000  startup         19.000000  23.0000  23.0000
992   Default  21.000000  numpy           21.000000  22.0000  22.0000
137   Default  20.000000  bayesian        20.000000  21.0000  21.0000
245   Default  9.000000   college         9.000000   20.0000  20.0000
260   Default  26.000000  communication   26.000000  19.0000  19.0000
337   Default  28.000000  currently       28.000000  18.0000  18.0000
790   Default  26.000000  lead            26.000000  17.0000  17.0000
1324  Default  11.000000  serve           11.000000  16.0000  16.0000
320   Default  29.000000  create          29.000000  15.0000  15.0000
973   Default  11.000000  nosql           11.000000  14.0000  14.0000
640   Default  15.000000  growth          15.000000  13.0000  13.0000
181   Default  8.000000   capital         8.000000   12.0000  12.0000
812   Default  15.000000  linux           15.000000  11.0000  11.0000
1333  Default  19.000000  shell           19.000000  10.0000  10.0000
977   Default  10.000000  nstitute        10.000000  9.0000   9.0000 
1310  Default  12.000000  security        12.000000  8.0000   8.0000 
237   Default  7.000000   coding          7.000000   7.0000   7.0000 
366   Default  7.000000   delivery        7.000000   6.0000   6.0000 
263   Default  30.000000  company         30.000000  5.0000   5.0000 
73    Default  16.000000  apache          16.000000  4.0000   4.0000 
670   Default  13.000000  history         13.000000  3.0000   3.0000 
322   Default  16.000000  creative        16.000000  2.0000   2.0000 
1038  Default  20.000000  panda           20.000000  1.0000   1.0000 
...       ...        ...       ...              ...     ...      ... 
1099  Topic3   2.926354   polytechnic     3.557921   1.7082  -6.2590 
444   Topic3   3.523382   eee             4.284599   1.7080  -6.0733 
712   Topic3   3.118700   initial         3.802547   1.7054  -6.1954 
1292  Topic3   5.966664   school          7.328563   1.6980  -5.5466 
1603  Topic3   5.273491   writing         6.470680   1.6990  -5.6701 
294   Topic3   9.478335   content         12.284655  1.6443  -5.0838 
746   Topic3   4.956383   investment      6.285494   1.6661  -5.7321 
977   Topic3   7.448234   nstitute        10.197977  1.5894  -5.3248 
1324  Topic3   7.950340   serve           11.118215  1.5683  -5.2596 
973   Topic3   8.130173   nosql           11.684691  1.5409  -5.2372 
791   Topic3   9.557657   leader          14.743950  1.4701  -5.0754 
497   Topic3   4.754640   estate          6.599817   1.5757  -5.7736 
640   Topic3   8.326126   growth          15.692411  1.2698  -5.2134 
1249  Topic3   5.384026   reviously       8.385190   1.4606  -5.6493 
1310  Topic3   6.697802   security        12.780382  1.2575  -5.4310 
1397  Topic3   8.162501   startup         19.436327  1.0360  -5.2332 
337   Topic3   9.763897   currently       28.701836  0.8254  -5.0541 
320   Topic3   9.862618   create          29.970592  0.7922  -5.0440 
230   Topic3   6.622144   cloud           15.246525  1.0697  -5.4424 
1493  Topic3   5.229040   t

In [32]:
# Topic-Keyword Matrix
df_topic_keywords = pd.DataFrame(lda_model.components_)

# Assign Column and Index
df_topic_keywords.columns = vectorizer.get_feature_names()
df_topic_keywords.index = topicnames

# View
#df_topic_keywords.head()

In [33]:
# Show top n keywords for each topic
def show_topics(vectorizer=vectorizer, lda_model=lda_model, n_words=10):
    keywords = np.array(vectorizer.get_feature_names())
    topic_keywords = []
    for topic_weights in lda_model.components_:
        top_keyword_locs = (-topic_weights).argsort()[:n_words]
        topic_keywords.append(keywords.take(top_keyword_locs))
    return topic_keywords

topic_keywords = show_topics(vectorizer=vectorizer, lda_model=lda_model, n_words=10)        

# Topic - Keywords Dataframe
df_topic_keywords = pd.DataFrame(topic_keywords)
df_topic_keywords.columns = ['Word '+str(i) for i in range(df_topic_keywords.shape[1])]
df_topic_keywords.index = ['Topic '+str(i) for i in range(df_topic_keywords.shape[0])]
df_topic_keywords

Word 0      Word 1       Word 2   Word 3      Word 4  \
Topic 0  classification  scikit      experienced  boost    simulation   
Topic 1  create          currently   leader       content  college      
Topic 2  client          understand  company      life     actionable   

              Word 5     Word 6      Word 7    Word 8 Word 9  
Topic 0  numpy        bayesian   processing  nlp       shell  
Topic 1  growth       startup    nosql       capital   serve  
Topic 2  ntelligence  operation  challenge   economic  field

In [41]:
# Define function to predict topic for a given text document.
nlp = spacy.load('en', disable=['parser', 'ner'])

def predict_topic(text, nlp=nlp):
    global sent_to_words
    global lemmatization

    # Step 1: Clean with simple_preprocess
    mytext_2 = list(sent_to_words(text))

    # Step 2: Lemmatize
    mytext_3 = lemmatization(mytext_2, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])

    # Step 3: Vectorize transform
    mytext_4 = vectorizer.transform(mytext_3)

    # Step 4: LDA Transform
    topic_probability_scores = lda_model.transform(mytext_4)
    topic = df_topic_keywords.iloc[np.argmax(topic_probability_scores), :].values.tolist()
    return topic, topic_probability_scores

# Predict the topic
predictSummarytopic = [combindedDatascientistTest['summary'][71]]

topic, prob_scores = predict_topic(text = predictSummarytopic)
print(prob_scores)
print(topic)

[[0.47953838 0.00872557 0.51173605]]
['client', 'understand', 'company', 'life', 'actionable', 'ntelligence', 'operation', 'challenge', 'economic', 'field']


In [43]:
from sklearn.metrics.pairwise import euclidean_distances

nlp = spacy.load('en', disable=['parser', 'ner'])

def similar_documents(text, doc_topic_probs, documents = datascienceSum, nlp=nlp, top_n=5, verbose=False):
    topic, x  = predict_topic(text)
    dists = euclidean_distances(x.reshape(1, -1), doc_topic_probs)[0]
    doc_ids = np.argsort(dists)[:top_n]
    if verbose:        
        print("Topic KeyWords: ", topic)
        print("Topic Prob Scores of text: ", np.round(x, 1))
        print("Most Similar Doc's Probs:  ", np.round(doc_topic_probs[doc_ids], 1))
    return doc_ids, np.take(documents, doc_ids)

In [45]:
# Get similar documents
jobDescription = pd.read_csv('jobdescription.csv');

jobtext = [jobDescription.JobDescription[2]];

doc_ids, docs = similar_documents(text=jobtext, doc_topic_probs=lda_output, documents = datascienceSum, top_n=1, verbose=True)
print('\n', docs[0][:500])
doc_ids

Topic KeyWords:  ['client', 'understand', 'company', 'life', 'actionable', 'ntelligence', 'operation', 'challenge', 'economic', 'field']
Topic Prob Scores of text:  [[0.  0.1 0.9]]
Most Similar Doc's Probs:   [[0.  0.1 0.9]]

 ['proven', 'leader', 'in', 'delivering', 'and', 'selling', 'engagements', 'that', 'align', 'business', 'processes', 'with', 'client', 'strategy', 'through', 'analytical', 'process', 'performance', 'improvements', 'ver', 'ten', 'years', 'of', 'global', 'consulting', 'experience', 'ed', 'engagements', 'for', 'fortune', 'companies', 'across', 'multiple', 'industries', 'including', 'oil', 'gas', 'healthcare', 'revenue', 'collection', 'and', 'manufacturing', 'extensive', 'experience', 'in', 'process', 'mprovements', 'modeling', 'optimization', 'performance', 'measurement', 'lean', 'six', 'sigma', 'and', 'offshore', 'development', 'addition', 'to', 'above', 'experience', 'saket', 'is', 'also', 'leader', 'within', 'booz', 'company', 'energy', 'utilities', 'operations', 

array([425])